# Polaron calculations using EPWpy

<table>
<tr>
<td width="50%">

Author: **Jon Lafuente-Bartolome**


In this notebook, we perform calculations of polarons. The theory and computational method are described in [Phys. Rev. Lett. **122**, 246403 (2019)](https://doi.org/10.1103/PhysRevLett.122.246403) and [Phys. Rev. B **99**, 235139 (2019)](https://doi.org/10.1103/PhysRevB.99.235139). 

Electrons and phonons are computed with Quantum ESPRESSO (QE), maximally-localized Wannier functions are computed with Wannier90, and electron-phonon matrix elements and polarons are computed with EPW.     
    
</td>
<td width="50%">

**MATCSSI**

<img src="https://matcssi.tacc.utexas.edu/media/filer_public_thumbnails/filer_public/9f/1e/9f1ebcd2-8f80-4142-bcdf-b9c262c6b62d/matccsi-home-banner.jpg__1400x1400_q85_subsampling-2.jpg" width="1000">

For running calculations
please visit [MATCSSI](https://matcssi.tacc.utexas.edu/)


</td>
</tr>
</table>

## NOTE: 

This notebook assumes that EPWpy is already installed in your active environment and that you are using the corresponding Jupyter kernel.
If you need guidance on installation or environment setup, please refer to the `installation_setup.ipynb` notebook.

## Calculations of self-trapped polarons

In this notebook we calculate the formation energy, wave function, and atomic displacements of self-trapped polarons in LiF using the [*ab initio* polaron equations](https://doi.org/10.1103/PhysRevB.99.235139).

Load required modules:

In [ ]:
from EPWpy import EPWpy as EP
from EPWpy.utilities import EPW_util 
from EPWpy.plotting import plot_polaron
import numpy as np
import matplotlib.pyplot as plt

### Define EPWpy object

Define general calculation parameters to be used throughout the workflow:

In [ ]:
# Set prefix
prefix='lif'

# Maximum number of cores to be used
cores = 64
print('Maximum number of cores to be used:', cores)

# Define EPWpy object
lif=EP.EPWpy({'prefix':'\''+prefix+'\'',
           'calculation':'\'scf\'',
           'ibrav':2,
           'nat':2,
           'ntyp':2,
           'atomic_species':['Li', 'F'],
           'atomic_pos':np.array([[0.0, 0.0, 0.0], 
                                  [-0.5, 0.5, 0.5]]), # in alat
           'mass':[6.941, 18.9984],
           'atoms':['Li', 'F'],
           'ecutwfc':'80',
           'celldm(1)':'7.67034',
           'pseudo_auto':True},
           system='lif')
#
lif.run_serial = True  # Run calculations synchronously 

Visualize crystal structure:

In [ ]:
%matplotlib widget

app = lif.display_lattice(supercell=[3,3,3],view={'wrap':False,
                                                  'show_bond_length':False,
                                                  'bond_length':2.5,
                                                  'bond_color':'g',
                                                  'atom_size_factor':100})

### Run scf, ph, and nscf calculations

Here we perform the self-consistent field calculation to obtain the electron charge density of LiF in the ground state. 
The calculation consists of three separate steps:
1. Apply the method `scf` to the object `lif`. This step specifies runtime parameters for the scf calculation.
2. Based on the properties defined at step 1 as well as other properties that are set by default within EPWpy, the method `prepare` creates the input file needed by QE.
3. The method `run` applied to the object `lif` instructs QE to perform the SCF calculation.

In [ ]:
# scf calculation
lif.scf(electrons={'conv_thr':'1.0d-12'}, kpoints={'kpoints':[[6, 6, 6]]}, name='scf')
lif.prepare(type_run='scf')
lif.run(cores, type_run='scf', parallelization='-nk 4')

Now we repeat a similar procedure for the phonon (`ph`) calculations on a coarse grid:

In [ ]:
# ph calculation
lif.ph(phonons={'nq1':6,
                'nq2':6,
                'nq3':6})
lif.prepare(type_run='ph')
lif.run(cores, type_run='ph', parallelization='-nk 4')

And proceed similarly for the `nscf` calculation:

In [ ]:
# nscf calculation
lif.nscf(system={'nbnd':15},
         kpoints={'grid':[6, 6, 6],
                  'kpoints_type': 'crystal'})
lif.prepare(type_run='nscf')
lif.run(cores, type_run='nscf', parallelization=' -nk 4')

### (Optional) Visualize phonon modes

Run a `dynmat` calculation to get phonon eigenvectors:

In [ ]:
lif.dynmat({'fildyn':'\'lif.dyn1\''},
           name='dynmat')
lif.prepare(type_run='dynmat')
lif.run(cores, 'dynmat')

Extract the polarization vector using `PH_utilities`:

In [ ]:
lif.ph_util = lif.PH_utilities()
pl_vec = lif.ph_util.polarization_vector[:,:,3:] # Get polarization vector
lif.scf_file = 'scf'
lif.pw_util = lif.PW_utilities()

Plot a given phonon mode:

In [ ]:
%matplotlib widget
from EPWpy.utilities.display_struct import *
mode = 5 # Choose the mode to display
Data = lif.get_Data(pl_vec[mode,:,:], supercell=[3,3,3])
fig, ani = animate_crystal_phonon(Data, alpha = 10, view = {'wrap':False,
                                                            'bond_length':2.8,
                                                            'show_bond_length':False,
                                                            'quiver_length':25,
                                                            'show_labels': False,
                                                            'atom_size_factor':100}, 
                                  bond_length = 6)

## (Exercise) Plot phonon dispersion bands

Follow similar steps as in the `transport.nb`notebook:
* Transform coarse **q**-mesh dynamical matrix to the interatomic force constant matrix in real space using `q2r.x`.
* Interpolate the dynamical matrix onto a **q**-path.
* Visualize phonon bands with the `plot_phonon_QE` utility of EPWpy (you will need to import the function using `from EPWpy.QE.band_util import BandUtil`; see electron band structure plot cells in `transport.nb`).

### EPW calculations on the coarse mesh

Now we calculate the electron-phonon matrix elements in the coarse mesh, and transform them to the Wannier representation.

We then proceed as in the other calculations.
First, we apply the method `epw` to the object `lif`. This step specifies runtime parameters for the EPW calculation. 
Then, we apply the method `prepare` to generate the input file, and `run` to perform the calculation.

In [ ]:
# epw coarse-mesh calculation
#
# set epw input variables
lif.epw(epwin={'wannierize':'.true.',
               'nbndsub':'3',
               'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'proj':['\'F : p\''],
               'wannier_plot':'.true.',
               'band_plot':'.true.',
               'lpolar':'.true.',
               'filkf':'\'./path.kpt\'',
               'filqf':'\'./path.kpt\'',
                },
        name='epw1')
#
# Generate filkf if needed
W=[0.5,0.75,0.25]
L=[0.0,0.5,0.0]
G=[0.0,0.0,0.0]
X=[0.5,0.5,0.0]
K=[0.375,0.75,0.375]
sympoints=[W,L,G,X,W,K]
lif.filkf(path=sympoints, length=[41, 41, 41, 41, 41], name='path.kpt')
#
# prepare and run
lif.prepare(type_run='epw1') 
lif.run(cores, type_run='epw1')

### (Optional) Plot Wannier functions

The Wannier functions can be visualized with the `plot_wannier` utility:

In [ ]:
lif_util = lif.EPW_utilities() # Get the EPW utility first 
lif_util.plot_wannier('lif_00001.cube',view={'grid':False,
                                             'pos_color':'crimson',
                                             'neg_color':'royalblue',
                                             'pos_alpha': 1.0,
                                             'neg_alpha': 1.0,
                                             'pos_iso_frac':0.15,
                                             'neg_iso_frac':0.15,
                                             'bond_size':3.0,
                                             'depthshade':False,
                                             'atom_kwargs':{'edgecolors':'k',
                                                            'linewidths':1.0}})

### Interpolation to fine mesh and solution of polaron equations

We now proceed with the interpolation onto a fine reciprocal-space grid, and the self-consistent solution of the polaron equations.
We prepare a `epw2` file to separate from the coarse-mesh calculation.

In [ ]:
lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'lpolar':'.true.',
               'plrn':'.true.',
               'restart_plrn':'.false.',
               'type_plrn':1,
               'init_plrn':1,
               'init_sigma_plrn':1.0,
               'niter_plrn':500,
               'conv_thr_plrn':1.0E-4,
               'ethrdg_plrn':1.0E-6,
               'adapt_ethrdg_plrn':'.true.',
               'init_ethrdg_plrn':1.0E-4,
               'nethrdg_plrn':20,
               'nkf1':6, 'nkf2':6, 'nkf3':6,
               'nqf1':6, 'nqf2':6, 'nqf3':6},
            name='epw2')
lif.prepare(1, type_run='epw2')
lif.run(cores, type_run='epw2')

### Visualization and post-processing

Once the polaron solution has been found, we can visualize its wave function and associated lattice displacements in real space, as well as their corresponding expansion coefficients in reciprocal space.

In [ ]:
# epw post-processing
lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'lpolar':'.true.',
               'plrn':'.true.',
               'restart_plrn':'.true.',
               'type_plrn':1,
               'cal_psir_plrn':'.true.',
               'step_wf_grid_plrn':4,
               'interp_Ank_plrn':'.true.',
               'interp_Bqu_plrn':'.true.',
               'filkf':'\'./path.kpt\'',
               'filqf':'\'./path.kpt\'',
               'nkf1':6, 'nkf2':6, 'nkf3':6,
               'nqf1':6, 'nqf2':6, 'nqf3':6},
            name='epw3')
lif.prepare(1,type_run='epw3')
lif.run(cores, type_run='epw3')

### Plot polaron wave function

We can visualize the polaron in real space, where arrows show the atomic displacements and the isosurface shows the polaron wave function.

In [ ]:
lif_util = lif.EPW_utilities() # Get the EPW utility first 
lif_util.plot_polaron(view={'quiver_length':10,
                            'depthshape':False,
                            'pos_alpha':1,
                            'atom_size_factor':30})

### Plot expansion coefficients

We can plot the interpolated expansion coefficients along a path in reciprocal space. We will use the same `path.kpt` file generated before:

In [ ]:
# Plot Ank coefficients
plot_polaron.plot_Ank_Bqv('Ank', prefix+'/epw/path.kpt', sympoints, prefix+'/epw/Ank.band.plrn')

In [ ]:
# Plot Bqv coefficients
plot_polaron.plot_Ank_Bqv('Bqv', prefix+'/path.kpt', sympoints, prefix+'/epw/Bmat.band.plrn')

## Extrapolation to the isolated polaron limit ($N_p\rightarrow\infty$)

The previous solution was obtained for a given reciprocal-space grid / real-space supercell.
To account for the spurious interactions between periodic images of polarons, we need to perform calculations on increasingly dense meshes and extrapolate to the dilute polaron limit.

We first define the grids we want to consider in which the corresponding formation energies will be computed, and prepare the input files:

In [ ]:
# List of k-point meshes to consider
klist = [8, 10, 12]

for k in klist:
    lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
                   'nbndsub':3,
                   'lpolar':'.true.',
                   'plrn':'.true.',
                   'restart_plrn':'.false.',
                   'type_plrn':1,
                   'init_plrn':1,
                   'init_sigma_plrn':1.0,
                   'niter_plrn':500,
                   'conv_thr_plrn':1.0E-4,
                   'ethrdg_plrn':1.0E-6,
                   'adapt_ethrdg_plrn':'.true.',
                   'init_ethrdg_plrn':1.0E-4,
                   'nethrdg_plrn':20,
                   'nkf1':str(k), 'nkf2':str(k), 'nkf3':str(k),
                   'nqf1':str(k), 'nqf2':str(k), 'nqf3':str(k)},
            name='epw4.'+str(k))

    #
    lif.prepare(type_run='epw3', name = 'epw', infile='epw4.'+str(k)+'.in')

We now run the calculations for each grid:

In [ ]:
# Run calculations
for k in klist:
    lif.run(cores, type_run='epw3', infile='epw4.'+str(k))

Now we perform a linear extrapolation to the infinite supercell limit from the computed data points:

In [ ]:
# Clear any previously stored figures before switching backend
plt.close('all')
%matplotlib inline

# Set unit cell volume in Bohr^3 (to convert Nk to inverse supercell size)
ucell_volume = 112.8044

# Read formation energies from output files
Eform = []
for k in klist:
    lif.epw_file = 'epw4.'+str(k)
    Eform.append(lif.Eform)

Nk = np.array(klist)
Eform = np.array(Eform)
                    
# Plot
plot_polaron.plot_EvsNk(ucell_volume, Nk, Eform)

## Polaron hopping barrier calculation

### Relatively dense grid calculation

In [ ]:
# Prepare epw input for fine mesh interpolation and polaron calculation
lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'etf_mem':0,
               'lpolar':'.true.',
               'plrn':'.true.',
               'restart_plrn':'.false.',
               'type_plrn':1,
               'init_plrn':1,
               'init_sigma_plrn':1.0,
               'niter_plrn':500,
               'conv_thr_plrn':1.0E-4,
               'ethrdg_plrn':1.0E-6,
               'adapt_ethrdg_plrn':'.true.',
               'init_ethrdg_plrn':1.0E-4,
               'nethrdg_plrn':20,
               'nkf1':6, 'nkf2':6, 'nkf3':6,
               'nqf1':6, 'nqf2':6, 'nqf3':6},
            name='epw2')
#
lif.prepare(type_run='epw2')
lif.run(cores, type_run='epw2')

### Shift the polaron displacement pattern by one unit cell

In [ ]:
import os
print(os.getcwd())
prefix=lif.prefix
print(prefix+'/epw/dtau.plrn')

# Read the dtau.plrn
dtau = EPW_util.read_dtau_plrn(prefix+'/epw/dtau.plrn')
# Shift it along x by one unit cell
shift_x = EPW_util.generate_dtau_disp(dtau, direction='x')
# Generate and all the intermediate structures
ntau = 21
EPW_util.write_dtau_disp(dtau, shift_x, ntau, fileout=prefix + '/epw/dtau_disp.plrn_')

#### Perform polaron calculations and save the total energy for all intermediate atomic displacement configurations

In [ ]:
# Prepare epw input for energy landscape calculation
lif.epw(epwin={'etf_mem':0,
               'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'plrn':'.true.',
               'restart_plrn':'.false.',
               'type_plrn':1,
               'init_plrn':6,
               'init_ntau_plrn':str(ntau),
               'init_sigma_plrn':1.0,
               'niter_plrn':1,
               'conv_thr_plrn':1.0E-4,
               'ethrdg_plrn':1.0E-6,
               'adapt_ethrdg_plrn':'.true.',
               'init_ethrdg_plrn':1.0E-4,
               'nethrdg_plrn':20,
               'io_lvl_plrn':0,
               'nkf1':6,
               'nkf2':6,
               'nkf3':6,
               'nqf1':6,
               'nqf2':6,
               'nqf3':6,
               'lpolar':'.true.',
               'eig_read':'.false.'},
            name='epw2.dtau')

# Prepare input file
lif.prepare(1, type_run='epw2', name='epw', infile='epw2.dtau.in')

# Run epw calculation
lif.run(cores, type_run='epw2', infile='epw2.dtau')

#### Plot the potential surface and extract the hopping barrier

In [ ]:
plt.close('all')
%matplotlib inline

prefix=lif.prefix
E_pot_surf = []
file = open(prefix + '/epw/epw2.dtau.out', 'r')
for line in file:
    if "Formation Energy at this " in line:
        E_pot_surf.append( float(line.split()[-1]) )
file.close()

font = {'family' : 'DejaVu Sans',
    'size'   : 18}
plt.rc('font', **font)

fig, ax = plt.subplots(1, figsize=(6,4))
scaling = np.linspace(0,1,ntau)
ax.plot(scaling, E_pot_surf, marker='o', markersize=5, linewidth=2, color='black')
ax.set_xlabel('Reaction coordinate')
ax.set_ylabel('Formation energy (eV)')

plt.show()


E_barrier = max(E_pot_surf) - min(E_pot_surf)

print('Hopping barrier (eV): ', E_barrier)

## (Exercise) Obtain the energy barrier in the isolated polaron limit

You will need to repeat the steps above, but using increasingly denser grids (larger BvK supercells) when calculating the energy landscape. 
Then you will need to collect all the data, and extrapolate the value of the energy at each point in the configuration coordinate to $N_p\rightarrow\infty$.